## Import Packages, Set Paths Dynamically

In [ ]:
import geopandas as gpd
import osmnx as ox
import folium
from shapely.geometry import box
from pathlib import Path
import yaml

In [ ]:
# get path to project root directory
project_root = Path.cwd().parents[0]

# build path to yaml config file
config_path = project_root / "configs"/"paths.yaml"

In [ ]:
# load yaml file into a python dictionary called paths
with open(config_path) as f:
    paths = yaml.safe_load(f)

paths

{'data': {'external': 'data/external',
  'raw': 'data/raw',
  'processed': 'data/processed',
  'results': 'results'},
 'outputs': {'dynamic_maps': 'outputs/maps/dynamic',
  'static_maps': 'output/maps/static',
  'figures': 'output/figures',
  'tables': 'outputs/tables'}}

In [ ]:
# build data directory using paths from yaml config
data_external = project_root / paths["data"]["external"]

# finally build path to our geojson file
settlements_path = data_external / "UNHCR_poc_boundaries-Uganda_attributed.geojson"

In [ ]:
# build output directory for maps using paths from the yaml config
maps_dir = project_root/paths['outputs']['dynamic_maps']
maps_dir.mkdir(parents=True, exist_ok = True)

# build output directory for osm data from the yaml config
output_dir = project_root / paths['data']['processed']
output_dir.mkdir(exist_ok=True)

## Load Settlements Dataset

In [ ]:
# load settlements into a gdf
settlements = gpd.read_file(settlements_path)

# inspect settlements gdf
settlements

name  objectid       pcode  iso3             name_2 name_alt  \
0       Ayilo 1    3441.0  UGAs004662   UGA            Ayilo 1     None   
1       Palabek   24832.0  UGAs032255   UGA            Palabek     None   
2       Palabek   27594.0  UGAs032271   UGA         Palabek RC     None   
3        Olua 1      21.0  UGAs001848   UGA             Olua 1     None   
4       Maaji I       NaN        None  None               None     None   
5     Oruchinga       NaN        None  None               None     None   
6      Bidibidi   21261.0  UGAs027216   UGA           Bidibidi     None   
7         Elema     178.0  UGAs001836   UGA              Elema     None   
8     Palorinya       NaN        None  None               None     None   
9         Rhino    4631.0  UGAs001883   UGA               Ocea     None   
10        Rhino    4684.0  UGAs990099   UGA   Rhino Settlement     None   
11        Rhino   26820.0  UGAs032256   UGA           Omugo RC     None   
12    Mungula 2     375.0  UGAs001854   UGA          Mungula 2     None   
13     Pagrinya   20314.0  UGAs004684   UGA           Pagrinya     None   
14       Lobule       NaN        None  None               None     None   
15    Mungula I   12606.0  UGAs004680   UGA            Mungula     None   
16  Kiryandongo       NaN        None  None               None     None   
17     Baratuku    3929.0  UGAs001954   UGA           Baratuku     None   
18       Boroli    3475.0  UGAs004663   UGA  Boroli Settlement     None   
19    Maaji III    2516.0  UGAs002612   UGA          Maaji III     None   
20     Alere II    2505.0  UGAs001953   UGA           Alere II     None   
21       Olua 2       NaN        None  None               None     None   
22        Agojo    2503.0  UGAs001951   UGA              Agojo     None   
23     Nakivale    4258.0  UGAs001945   UGA           Nakivale     None   
24     Nakivale   27592.0  UGAs032268   UGA        Kabazana RC     None   
25     Nyumanzi    3515.0  UGAs004664   UGA           Nyumanzi     None   
26      Mirieyi    2371.0  UGAs001598   UGA            Mirieyi     None   
27       Imvepi     168.0  UGAs990098   UGA          Imvepi RC     None   
28       Imvepi    3930.0  UGAs004668   UGA  Imvepi Settlement     None   
29     Maaji II    2696.0  UGAs002611   UGA           Maaji II     None   
30     Kyaka II     416.0  UGAs001941   UGA          Sweswe RC     None   
31     Kyaka II    3585.0  UGAs002986   UGA           Kyaka II     None   
32    Rwamwanja   27588.0  UGAs032267   UGA          Mahani RC     None   
33     Kyagwali       NaN        None  None               None     None   
34      Ayilo 2    4758.0  UGAs004661   UGA            Ayilo 2     None   
35        Oliji     580.0  UGAs001956   UGA              Oliji     None   

    loc_type loc_subtype    createdate            createby closedate  \
0       35.0         ***  1.401667e+12     orand@unhcr.org      None   
1       35.0         ***  1.496016e+12     saint@unhcr.org      None   
2       37.0        None  1.541376e+12     orand@unhcr.org      None   
3       35.0         ***  8.862912e+11                None      None   
4        NaN        None           NaN                None      None   
5        NaN        None           NaN                None      None   
6       35.0         ***  1.476144e+12     saint@unhcr.org      None   
7       35.0         ***  6.942240e+11                None      None   
8        NaN        None           NaN                None      None   
9       37.0         ***  7.677504e+11                None      None   
10      35.0         ***  1.165277e+12                None      None   
11      37.0         ***  1.524182e+12     orand@unhcr.org      None   
12      35.0         ***  8.415360e+11                None      None   
13      35.0         ***  1.472170e+12     orand@unhcr.org      None   
14       NaN        None           NaN                None      None   
15      35.0         ***  1.431994e+12  chatelli@unhcr.org      None   
16       Na

## Explore Settlement Dataset
Let's get some basic information about the Uganda settlement planning boundaries starting with the CRS, length, and geometry types. We'll then reproject, perform area calculations, and map. 

In [ ]:
# print overview of dataset
overview_dict  = {
    "CRS": str(settlements.crs),                                 
    "Number of features": len(settlements),                       
    "Geometry types": settlements.geom_type.unique().tolist(),                 
}

overview_dict

{'CRS': 'EPSG:4326',
 'Number of features': 36,
 'Geometry types': ['MultiPolygon', 'Polygon']}

Lets find the best UTM zone for our data. Then we can reproject to that and get some area measures. 

In [ ]:
import math 

# define a function to calculate UTM zone and corresponding EPSG code from lat and lon
def get_utm_epsg(lon, lat):
    """
    Return EPSG code for UTM zone based on latitude and longitude

    Args: 
        lon (float): Longitude in degrees
        lat (float): Latitude in degrees
    
    Returns:
        int: EPSG code for the corresponding UTM zone 
    """
    zone = math.floor((lon + 180)/6)+1
    if lat >= 0:
        return 32600 + zone
    else: 
        return 32700 + zone

In [ ]:
# derive the "centroid" of the dataset
mean_lon = settlements.geometry.representative_point().x.mean() # use representative point because data is in GCS
mean_lat = settlements.geometry.representative_point().y.mean()

# define a sensible utm_zone for our analysis
epsg = get_utm_epsg(mean_lon, mean_lat)
epsg

32636

In [ ]:
# define area_km2 column 
settlements['area_km2'] = settlements.to_crs(crs = epsg).area/1e6
settlements.head(2)

name  objectid       pcode iso3   name_2 name_alt  loc_type loc_subtype  \
0  Ayilo 1    3441.0  UGAs004662  UGA  Ayilo 1     None      35.0         ***   
1  Palabek   24832.0  UGAs032255  UGA  Palabek     None      35.0         ***   

     createdate         createby closedate    updatedate updateby source  \
0  1.401667e+12  orand@unhcr.org      None  1.611240e+12    ORAND  UNHCR   
1  1.496016e+12  saint@unhcr.org      None  1.611240e+12    ORAND  UNHCR   

   unhcr_assist     footnote      comments  status  \
0           1.0  RE-2013-SSD  Northern UGA     1.0   
1           NaN               Northern UGA     1.0   

                                 globalid       lat        lon   date_str  \
0  {FD926792-2F62-48EE-8150-21AB071AAF91}  3.296111  31.934722 2014-06-01   
1  {1E5A0908-F9A7-4258-91E3-BAC7105155DE}  3.364856  32.412692 2017-05-28   

                                            geometry    area_km2  
0  MULTIPOLYGON (((31.93172 3.30525, 31.93109 3.3...    4.067789  
1  POLYGON ((32.56756 3.3585, 32.56752 3.35891, 3...  211.518165

In [ ]:
# get a summary of refugee settlement areas in Uganda
settlements['area_km2'].drop_duplicates().describe() # dropping duplicate observations

count     30.000000
mean      81.662585
std      184.556020
min        0.136626
25%        1.438549
50%        4.473430
75%       44.545599
max      790.929713
Name: area_km2, dtype: float64

Let's use follium to map the refugee settlement planning boundaries over high res aerial imagery, then we'll begin focussing on Nakivale, one of the larger settlements. 

In [ ]:
# define simple_settlements, json generalizable
simple_settlements = settlements.drop_duplicates(subset = 'name').reset_index(drop = True)
simple_settlements = simple_settlements.drop(
    columns=simple_settlements.select_dtypes(include=['datetime64[ns]', 'datetime64[ns, UTC]']).columns
)

# define a point to center the display
center_x = simple_settlements.geometry.iloc[1].centroid.x
center_y = simple_settlements.geometry.iloc[1].centroid.y
center_point = [center_y, center_x]

# create interactive folium map
m = folium.Map(
    location = center_point,
    zoom_start = 10,
    tiles = None
)

# Add Esri World Imagery (very high resolution)
folium.TileLayer(
    tiles='https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
    attr='Esri World Imagery',
    name='Esri Aerial Imagery'
).add_to(m)

folium.GeoJson(
    simple_settlements,
    name='Settlements',
    style_function=lambda x: {
        'fillColor': 'white',
        'color': 'black',
        'weight': 2,
        'fillOpacity': 0.2
    },
    tooltip=folium.GeoJsonTooltip(fields=[c for c in ['name', 'status', 'area_km2']])
).add_to(m)

folium.LayerControl().add_to(m)
m.save(maps_dir/"all_settlements_esri_overlay.html")
m

In [ ]:
from shapely.validation import make_valid

def get_osm_features_for_settlement(settlements_gdf, name, tags):
    """
    Query OSM features for a specific settlement in settlements_gdf by name

    Params:
    settlements_gdf : GeoDataFrame
        GeoDataFrame containing settlement polygons with a 'name' column

    name : str
        Name of the settlement to query

    tags: dict
        OSM tags to query, e.g. {"highway: True}

    Returns:
        
    """

    # match settlement by name
    match = settlements_gdf[settlements_gdf["name"].str.lower() == name.lower()]
    if match.empty:
        raise ValueError(f"No settlement found with name '{name}'")
    
    # extract geometry of settlement
    geom = match.geometry.iloc[0]

    # query osm API
    features = ox.features_from_polygon(geom, tags)

    return features

In [51]:
roads_and_paths = get_osm_features_for_settlement(simple_settlements, "Nakivale", {"highway": True})

In [52]:
import pandas as pd

# set display settings 
pd.set_option("display.max_columns", None)

# examine the full dataset
roads_and_paths.head(5)

geometry crossing   highway traffic_sign  \
element id                                                                      
node    5612340201  POINT (30.81722 -0.79545)      NaN  give_way          NaN   
        5612340204  POINT (30.81718 -0.79533)    zebra  crossing          NaN   
        5612340205  POINT (30.81708 -0.79531)    zebra  crossing          NaN   
        5612340434  POINT (30.81684 -0.79581)    zebra  crossing          NaN   
        5612340435  POINT (30.81688 -0.79576)      NaN  give_way     give_way   

                   surface source noname abutters easy_overtaking  ele  \
element id                                                               
node    5612340201     NaN    NaN    NaN      NaN             NaN  NaN   
        5612340204     NaN    NaN    NaN      NaN             NaN  NaN   
        5612340205     NaN    NaN    NaN      NaN             NaN  NaN   
        5612340434     NaN    NaN    NaN      NaN             NaN  NaN   
        5612340435     NaN    NaN    NaN      NaN             NaN  NaN   

                   ele:local foot incline lanes  lit maxspeed  \
element id                                                      
node    5612340201       NaN  NaN     NaN   NaN  NaN      NaN   
        5612340204       NaN  NaN     NaN   NaN  NaN      NaN   
        5612340205       NaN  NaN     NaN   NaN  NaN      NaN   
        5612340434       NaN  NaN     NaN   NaN  NaN      NaN   
        5612340435       NaN  NaN     NaN   NaN  NaN      NaN   

                   maxspeed:agricultural maxspeed:type priority smoothness  \
element id                                                                   
node    5612340201                   NaN           NaN      NaN        NaN   
        5612340204                   NaN           NaN      NaN        NaN   
        5612340205                   NaN           NaN      NaN        NaN   
        5612340434                   NaN           NaN      NaN        NaN   
        5612340435                   NaN           NaN      NaN        NaN   

                   source:maxspeed tracktype width maxspeed:hgv maxspeed:psv  \
element id                                                                     
node    5612340201             NaN       NaN   NaN          NaN          NaN   
        5612340204             NaN       NaN   NaN          NaN          NaN   
        5612340205             NaN       NaN   NaN          NaN          NaN   
        5612340434             NaN       NaN   NaN          NaN          NaN   
        5612340435             NaN       NaN   NaN          NaN          NaN   

                   name oneway service bridge layer priority_road junction  \
element id                                                                   
node    5612340201  NaN    NaN     NaN    NaN   NaN           NaN      NaN   
        5612340204  NaN    NaN     NaN    NaN   NaN           NaN      NaN   
        5612340205  NaN    NaN     NaN    NaN   NaN           NaN      NaN   
        5612340434  NaN    NaN     NaN    NaN   NaN           NaN      NaN   
        5612340435  NaN    NaN     NaN    NaN   NaN           NaN      NaN   

                   footway barrier colour height kerb kerb:colour kerb:height  \
element id                                                                      
node    5612340201     NaN     NaN    NaN    NaN  NaN         NaN         NaN   
        5612340204     NaN     NaN    NaN    NaN  NaN         NaN         NaN   
        5612340205     NaN     NaN    NaN    NaN  NaN         NaN         NaN   
        5612340434     NaN     NaN    NaN    NaN  NaN         NaN         NaN   
        5612340435     NaN     NaN    NaN    NaN  NaN         NaN         NaN   

                   landcover bicycle horse wheelchair access informal  \
element id                                                              
node    5612340201       NaN     NaN   NaN        NaN    NaN      NaN   
        5612340204       NaN     NaN   NaN        Na

In [53]:
# print the different types of roadway for filtering
roads_and_paths['highway'].value_counts()

highway
track             627
path              447
unclassified      362
residential       127
service            32
tertiary           29
footway            13
secondary          11
crossing            9
primary             8
give_way            7
platform            6
secondary_link      2
pedestrian          1
Name: count, dtype: int64

In [54]:
aoi = simple_settlements[simple_settlements['name'].str.lower() == "nakivale"]

# filtering for urban buildup, highway and roadways
roads = roads_and_paths[roads_and_paths['highway'].isin(['primary', 'secondary', 'tertiary',
    'unclassified', 'service', 'give_way', 'crossing', 'secondary_link', 'platform'])].copy().clip(aoi)

# filtering for more informal development, footpaths and residential
footpaths = roads_and_paths[roads_and_paths['highway'].isin(['path', 'footway', 'track', 'pedestrian', 'steps', 'residential'])].copy().clip(aoi)

roads = roads[roads.length > 0.0001]
footpaths = footpaths[footpaths.length > 0.0001]

roads.to_file(output_dir / "nakivale_osm_roads_clean_v1.geojson", driver="GeoJSON")
footpaths.to_file(output_dir / "nakivale_osm_footpaths_clean_v1.geojson", driver="GeoJSON")

C:\Users\Zachary\AppData\Local\Temp\ipykernel_16508\2232338983.py:10: UserWarning: Geometry is in a geographic CRS. Results from 'length' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  roads = roads[roads.length > 0.0001]
C:\Users\Zachary\AppData\Local\Temp\ipykernel_16508\2232338983.py:11: UserWarning: Geometry is in a geographic CRS. Results from 'length' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  footpaths = footpaths[footpaths.length > 0.0001]


In [55]:
center_x = aoi.geometry.centroid.x
center_y = aoi.geometry.centroid.y
center_point = [center_y, center_x]

m2 = folium.Map(location = center_point,
                 zoom_start = 12, 
                 tiles = None
                 )

folium.TileLayer(
    tiles='https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
    attr='Esri World Imagery',
    name='Esri Aerial Imagery',
    show = True
).add_to(m2)

folium.TileLayer(
    tiles='https://mt1.google.com/vt/lyrs=s&x={x}&y={y}&z={z}',
    attr='Google Maps Satellite Imagery',
    name='Google Maps Satellite Imagery',
    show =False
).add_to(m2)

folium.GeoJson(aoi,
               name = "Nakivale",
               style_function = lambda x: {
                   'color': "white",
                   'weight': 3}).add_to(m2)

folium.GeoJson(roads,
               name = "roads",
               style_function=lambda x:{
                   'color': "#ff1500",
                   'weight': 2,
               },
               tooltip = folium.GeoJsonTooltip(fields= [c for c in ['crossing', 'highway']])
               ).add_to(m2)

folium.GeoJson(footpaths,
               name = 'footpaths',
               style_function = lambda x:{
                   'color': "#fff700",
                   'weight': 2
               },
               tooltip = folium.GeoJsonTooltip(fields= [c for c in ['crossing', 'highway']])
               ).add_to(m2)

folium.LayerControl().add_to(m2)
m2.save(maps_dir/"nakivale_osm_overlay.html")
m2

C:\Users\Zachary\AppData\Local\Temp\ipykernel_16508\2461178273.py:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  center_x = aoi.geometry.centroid.x
C:\Users\Zachary\AppData\Local\Temp\ipykernel_16508\2461178273.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  center_y = aoi.geometry.centroid.y
c:\Users\Zachary\anaconda3\envs\uganda-osm\Lib\site-packages\folium\utilities.py:103: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  float(coord)
c:\Users\Zachary\anaconda3\envs\uganda-osm\Lib\site-packages\folium\utilities.py:109: FutureWarning: Calling float on a single element Series is deprecated and will raise a T